# EPS 109 Final Project
Timothy Elnitiarta

In [ ]:
import matplotlib.pyplot as plt
import numpy as np
from matplotlib.animation import FFMpegWriter
from scipy.interpolate import interp1d

%matplotlib qt

In [ ]:
# constants
n_glen = 3
rho = 917 # kg/m^3
A_glen = 24E-25 # s^-1 Pa^-n_glen
g = 9.8 # meters/s^2

# time conversions
hours = 3600
days = 24*hours
years = 365*days

# parameters
alpha_deg = 5
alpha_rad = np.radians(alpha_deg)

beta_deg = 2
beta_rad = np.radians(beta_deg)

H_0 = 200 # meters

eta = (2**(n_glen)*A_glen*(rho*g*H_0*(beta_rad-alpha_rad))**(n_glen-1))**(-1) # effective viscosity

ab = 0.05 # maximum ablation rate in m/day
ab = ab/86400

eq_line = 500 # equilibrium line position in meters

In [ ]:
def dx_back(x):
    dx = np.concatenate([[1], x[1:]-x[:-1]])
    return(dx)
    
def dx_front(x):
    dx = np.concatenate([x[1:]-x[:-1], [1]])
    return(dx)
    
def ddx_back(x, y):
    n = len(y)
    ddx = np.identity(n)-np.roll(np.identity(n), 1, axis=0)
    ddx[0,:] = 0
    ddx = np.matmul(ddx, y)
    dx = dx_back(x)
    ddx = ddx/dx
    return ddx
    
def ddx_front(x, y):
    n = len(y)
    ddx = np.roll(np.identity(n), -1, axis=0)-np.identity(n)
#     ddx[-1,:] = 0
    ddx[-1,:] = ddx[-2,:]
    
    ddx = np.matmul(ddx, y)
    dx = dx_front(x)
    ddx = ddx/dx
    return ddx

def ddx2_back(x, y):
    ddx2 = ddx_front(x,y)-ddx_back(x,y)
    dx = dx_back(x)
    ddx2 = ddx2/dx
    return(ddx2)

def surf_x(x, x_surf, surf):
    f = interp1d(x_surf, surface, kind='cubic')
    return(f(x))

def time_step_z_mark(x_mark, z_mark, x, surf, gamma, dt, alpha, dx=1):
    surf_0 = surf_x(x_mark, x, surf)
    surf_plus = surf_x(x_mark + dx, x, surf)
    surf_minus = surf_x(x_mark - dx, x, surf)
    dhdx_plus = (surf_plus - surf_0)/dx
    dhdx_minus = (surf_0 - surf_minus)/dx
    
#     gamma = rho*g/eta/3*dt
    z_new = z_mark + gamma * dt / 3 * (3*np.power(surf_0,2)*dhdx_minus*(dhdx_minus*np.cos(alpha)+np.sin(alpha))
                              + np.power(surf_0,3)/dx*(dhdx_plus-dhdx_minus)*np.cos(alpha))
    z_new[z_new<0] = 0
    return(z_new)
    
def time_step_x_mark(x_mark, z_mark, x, surf, gamma, dt, alpha, dx=1):
    surf_0 = surf_x(x_mark, x, surf)
    surf_plus = surf_x(x_mark + dx, x, surf)
    surf_minus = surf_x(x_mark - dx, x, surf)
    dhdx_plus = (surf_plus - surf_0)/dx
    dhdx_minus = (surf_0 - surf_minus)/dx
    
    u = gamma * (dhdx_minus*np.cos(alpha)-np.sin(alpha))*(0.5*np.power(z_mark,2)-surf_0*z_mark)
    x_new = x_mark + dt * u
    return(x_new)   
    
def time_step_z_surf(x, surf, gamma, dt, alpha):
    surf_new = surf + gamma * dt / 3 * (3*np.power(surf,2)*ddx_back(x,surf)*(ddx_back(x,surf)*np.cos(alpha)+np.sin(alpha))
                              + np.power(surf,3)/dx_back(x)*(ddx_front(x,surf)-ddx_back(x,surf))*np.cos(alpha))
    return(surf_new)
        
def time_step_x_surf(x, surf, gamma, dt, alpha):
#     gamma = rho*g/eta
    u = gamma * (ddx_back(x,surf)*np.cos(alpha)-np.sin(alpha))*(0.5*np.power(surf,2)-surf*surf)
    x_new = x + dt * u
    return(x_new)

def ablation_rate(x, ab, eq_line):
    '''
    Linear ablation pattern from 0 at equilibrium line to rate ab at terminus 
    '''
    ab_rate = x - eq_line
    ab_rate = ab_rate/2 + np.abs(ab_rate)/2
    ab_rate = ab_rate/np.max(ab_rate) * ab
    return(ab_rate)

In [ ]:
def convert_time(iteration, dt):
    time = dt*(iteration+1)
    t_year = int(time//(years))
    t_day = int((time-years*t_year)//(days))
    t_hour = (time - t_year*years - t_day*days)/hours
    time = f"{t_year}y {t_day}d {t_hour:.2f}h"
    return(time)

def rotate_frame(coords, alpha, vshift):
    rot_mat = np.array([[np.cos(alpha_rad), -np.sin(alpha_rad)],
                   [np.sin(alpha_rad), np.cos(alpha_rad)]])
    coords = np.matmul(coords, rot_mat)
    coords[:,1]+=vshift
    return(coords)
    

def display_fig(x, surface, x_mark, z_mark, eq_line, time, alpha):
    x_disp = np.concatenate([[0],x, [x[-1]]])
    surface_disp = np.concatenate([[surface[0]],surface,[0]])
    surface_coords = np.stack([x_disp, surface_disp], axis=1)
    marker_coords = np.stack([x_mark,z_mark], axis=1)
    eq_coords = np.array([[eq_line,0], [eq_line,300]])
    bedrock_coords = np.stack([np.linspace(0,1500,11), np.zeros(11)], axis=1)
    vshift = np.sin(alpha)*np.max(bedrock_coords[:,0])
    
    surface_coords = rotate_frame(surface_coords, alpha, vshift)
    surface_coords[0,1] -= surface_coords[0,0] * (surface_coords[2,1]-surface_coords[1,1])/(surface_coords[2,0]-surface_coords[1,0])
    surface_coords[0,0] = 0
    
    marker_coords = rotate_frame(marker_coords, alpha, vshift)
    eq_coords = rotate_frame(eq_coords, alpha, vshift)
    bedrock_coords = rotate_frame(bedrock_coords, alpha, vshift)
    
    
    plt.clf()
    
    plt.plot(surface_coords[:,0], surface_coords[:,1], color='mediumturquoise', label='ice surface')
    plt.plot(marker_coords[:,0], marker_coords[:,1], 'ro', ms=3, label='flow markers')
    plt.plot(eq_coords[:,0], eq_coords[:,1], 'r--', label='equilibrium line')
    plt.plot(bedrock_coords[:,0], bedrock_coords[:,1], color='brown', label='bedrock')
    plt.fill_between(surface_coords[:,0], surface_coords[:,1], color='mediumturquoise', alpha=0.5)
    plt.fill_between(bedrock_coords[:,0], bedrock_coords[:,1], color='peru')

    
    plt.title(f"Time: {time}")
    plt.xlabel('distance (meters)')
    plt.ylabel('elevation (meters)')
    plt.xlim(0,1500)
    plt.ylim(0,500)
    plt.legend()
    
    plt.tight_layout()
    plt.show()
    plt.draw()
    plt.pause(0.01)

In [ ]:
def init_ice_surface(x, H, power):
    f = lambda x: np.power(np.max(x)+20-x, 1/power)
    surf = f(x).real
    surf = surf * H / np.max(surf)
    return(surf)

In [ ]:
x = np.linspace(0,1000,101)
dx_0 = x[1]-x[0]
surface = init_ice_surface(x, H_0, 3)

n_mark = 5
x_mark = np.ones(n_mark)*20
z_mark = np.linspace(H_0/(n_mark+1),n_mark*H_0/(n_mark+1),n_mark)

runtime = 3*years
dt = 1200 # 20 minute time step
iterations = int(np.ceil(runtime/dt))
gamma = rho * g / eta

frame_rate = 15 # fps
capture_rate = 1*years/dt/8/frame_rate # animate one year every 8 seconds
plt.rcParams['figure.figsize'] = [9,3]


metadata = dict(title='2D Glacial Flow Cross Section', artist='Timothy Elnitiarta',comment='')
writer = FFMpegWriter(fps=frame_rate, metadata=metadata)
fig = plt.figure(dpi=200)

with writer.saving(fig, "animation3.mp4", dpi=200):
    display_fig(x,surface, x_mark, z_mark, eq_line, 0, alpha_rad)
    writer.grab_frame()

    for iteration in range(iterations):
#         break

        x_new = time_step_x_surf(x, surface, gamma, dt, alpha_rad)
        surface = time_step_z_surf(x, surface, gamma, dt, alpha_rad)
        surface = surface - ablation_rate(x, ab, eq_line) * dt
        x_new = x_new[surface>0]
        surface = surface[surface>0]

        x_mark_new = time_step_x_mark(x_mark, z_mark, x, surface, gamma, dt, alpha_rad)
        z_mark = time_step_z_mark(x_mark, z_mark, x, surface, gamma, dt, alpha_rad)

        x = np.copy(x_new)
        x_mark = np.copy(x_mark_new)


        if x[0]>dx_0:
            x = np.concatenate([[0], x])
            surface = np.concatenate([[surface[0]], surface])


        if (iteration+1)%capture_rate==0 or (iteration+1)==iterations:
            display_fig(x,surface, x_mark, z_mark, eq_line, convert_time(iteration, dt), alpha_rad)
            writer.grab_frame()
        